In [1]:
# =======================================================
# Unified User Configuration and Environment & Imports
# =======================================================
import pandas as pd
import Metadata.utils as ut
import sys, torch, warnings

sys.path.append('/home/student2025/shirx2025/MUSK-surv')

# gdc-client.exe path
GDC_CLIENT = r"/home/student2025/shirx2025/MUSK-surv/TCGA_DATA/gdc-client/gdc-client"

# manifest file root directory
GDC_ROOT   = r"/home/student2025/shirx2025/MUSK-surv/TCGA_DATA/gdc-client"   

# Parent directory for download directories
DOWNLOAD_PARENT = r"/home/student2025/shirx2025/MUSK-surv/TCGA_DATA"         

# NPZ file output directory
OUT_PARENT = r"/home/student2025/shirx2025/MUSK-surv/PATIENT_NPZ_FINAL"             

# List of cancer types
CANCERS = ["ACC", "COAD", "ESCA", "LIHC", "PAAD", "READ", "STAD", "BLCA", "BRCA", "CESC", "CHOL", 
           "DLBC", "GBM", "HNSC", "KICH", "KIRC", "KIRP", "LGG", "LUAD", "LUSC", "MESO", "OV", 
           "PCPG", "PRAD","SARC", "SKCM", "TGCT", "THCA", "THYM", "UCEC", "UCS", "UVM"]  

# --- Device  ---
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
USE_FP16       = True

# --- Survival endpoint ---
ENDPOINT            = "PFS"               # {"OS","DSS","PFS","RFS"}
ONLY_DIAGNOSTIC     = True                # Whether to keep diagnostic slices (default True)

# --- MUSK encoders ---
MUSK_TEXT_CKPT      = r"/home/student2025/shirx2025/MUSK-surv/MUSK/musk/models/model.safetensors"  # MUSK weights(local)

# --- WSI tiling / features ---
TARGET_MAG     = 20
TILE_SIZE      = 512
STEP           = 512
MIN_TISSUE     = 0.40
BATCH_SIZE     = 128
USE_FP16       = True
MS_AUG         = False
SEED           = 42

# Whether to delete directory after the NPZ is successfully generated (default True)
DELETE_RAW_AFTER = False

# --- Other setups ---
# Ignore warnings
warnings.filterwarnings("ignore")
# Set pandas display options
pd.set_option("display.max_columns", 200)
# Set the random seed for reproducibility
ut.set_seed()

In [2]:
# =======================================================
# Imports & Load Models
# =======================================================
import torchvision
import torch.nn as nn
from load_model import load_musk_model
from timm.data.constants import IMAGENET_INCEPTION_MEAN, IMAGENET_INCEPTION_STD

# --- Image Preprocess ---
vision_preprocess = torchvision.transforms.Compose([
        torchvision.transforms.Resize(384, interpolation=3, antialias=True),
        torchvision.transforms.CenterCrop((384, 384)),
        torchvision.transforms.ToTensor(),
        torchvision.transforms.Normalize(mean=IMAGENET_INCEPTION_MEAN, std=IMAGENET_INCEPTION_STD),
    ])

# --- Load MUSK model ---
model, DEVICE = load_musk_model(MUSK_TEXT_CKPT, device=DEVICE,fp16=False)

# --- Invocation GPU
if torch.cuda.device_count() > 1:
    print(f"Use {torch.cuda.device_count()} GPUs")
    model = nn.DataParallel(model, device_ids=[0, 1])


                   Model loading verification report                    

【1. Weighted Matching Degree】
  ✓ Successfully loaded: 974 parameters
  ✓ Missing: 0
  ✓ superfluous: 0

【2. Weighted Health Check】
  ✓ NaN: 0
  ✓ Inf: 0
  ✓ zero: 0

【3. Forward Pass Test】
  ✓ Test passed
  ✓ Output type: tuple (containing 2 elements)
  ✓ Main output shape: [1, 1024]
  ✓ Main output range: [-0.1409, 0.1726]

                     ✓ Model loaded successfully!                     

Use 2 GPUs


In [ ]:
# =======================================================
# Main Processing Loop
# =======================================================
import os, glob
import numpy as np
from export import export_npz_for_cancer
# --- Main Process ---
all_summaries = []

# Iterate all cancers
for code in CANCERS:
    # Check if the server allows access to the GDC
    if not ut.check_reach_gdc():
        print("[NET] api.gdc.cancer.gov:443 is inaccessible: Please configure a proxy/whitelist or switch to offline downloading.")
        break

    # Process each cancer
    print("\n" + "="*72)
    print(f"### Start cancer: {code}")
    print("="*72)
    summary = export_npz_for_cancer(code,GDC_ROOT, GDC_CLIENT,
                          DOWNLOAD_PARENT, OUT_PARENT, model, vision_preprocess,
                          ENDPOINT, ONLY_DIAGNOSTIC, DELETE_RAW_AFTER)
    if isinstance(summary, pd.DataFrame):
        summary["cancer"] = code
        all_summaries.append(summary)

# Aggregate results
if all_summaries:
    final = pd.concat(all_summaries, ignore_index=True)
    print("\n=== Overall summary ===")
    print(final.groupby(["cancer","saved"]).size().unstack(fill_value=0))
    final.to_csv(os.path.join(OUT_PARENT, "NPZ", "npz_summary_all_cancers.csv"), index=False)
else:
    print("\n[INFO] No summaries produced.")

# Quick validation
cands = sorted(glob.glob(os.path.join(OUT_PARENT, "*.npz")))
if cands:
    p = cands[0]; z = np.load(p, allow_pickle=True)
    print("[NPZ]", p, "->", z.files)

Found 12039 patches. Preparing DataLoader...

Slide: TCGA-UY-A8OD-01Z-00-DX1.3985C497-D586-4AB9-A635-63A7946C5A2E.svs
Time Statistics:
tiles_from_wsi      :  29.9897 s (16.71%)
encode_patches      : 149.5218 s (83.29%)
--------------------------------------------------
Total Time          : 179.5115 s (100.00%)
Speed               : 67.1 patches/sec



Scanning slide: TCGA-BT-A20R-01Z-00-DX1.38320FC0-F1E5-401B-9336-D77796456B30.svs...
Found 14276 patches. Preparing DataLoader...

Slide: TCGA-BT-A20R-01Z-00-DX1.38320FC0-F1E5-401B-9336-D77796456B30.svs
Time Statistics:
tiles_from_wsi      :  41.2888 s (17.78%)
encode_patches      : 190.8907 s (82.22%)
--------------------------------------------------
Total Time          : 232.1795 s (100.00%)
Speed               : 61.5 patches/sec



Scanning slide: TCGA-XF-AAN2-01Z-00-DX1.EB523A3A-0DE0-4FFC-9FE7-CF4FB2FB36CF.svs...
Found 11691 patches. Preparing DataLoader...

Slide: TCGA-XF-AAN2-01Z-00-DX1.EB523A3A-0DE0-4FFC-9FE7-CF4FB2FB36CF.svs
Time Statistics:
tiles_from_wsi      :  48.3853 s (23.16%)
encode_patches      : 160.5557 s (76.84%)
--------------------------------------------------
Total Time          : 208.9411 s (100.00%)
Speed               : 56.0 patches/sec



Scanning slide: TCGA-XF-A8HB-01Z-00-DX1.D6874152-D20A-4CA4-8E8B-8CBAB5F7D7B5.svs...
Found 11110 patches. Preparing DataLoader...

Slide: TCGA-XF-A8HB-01Z-00-DX1.D6874152-D20A-4CA4-8E8B-8CBAB5F7D7B5.svs
Time Statistics:
tiles_from_wsi      :  47.5973 s (24.14%)
encode_patches      : 149.5712 s (75.86%)
--------------------------------------------------
Total Time          : 197.1684 s (100.00%)
Speed               : 56.3 patches/sec



Scanning slide: TCGA-FJ-A3ZE-01Z-00-DX2.147C2363-55A3-4C02-BAF5-4F1256E30542.svs...
Found 20971 patches. Preparing DataLoader...

Slide: TCGA-FJ-A3ZE-01Z-00-DX2.147C2363-55A3-4C02-BAF5-4F1256E30542.svs
Time Statistics:
tiles_from_wsi      :  80.3839 s (22.49%)
encode_patches      : 277.0480 s (77.51%)
--------------------------------------------------
Total Time          : 357.4320 s (100.00%)
Speed               : 58.7 patches/sec



...

Scanning slide: TCGA-GC-A3I6-01Z-00-DX1.47650F7B-0AD3-49C9-AB9E-40383C7D07AC.svs...
Found 2541 patches. Preparing DataLoader...



Slide: TCGA-GC-A3I6-01Z-00-DX1.47650F7B-0AD3-49C9-AB9E-40383C7D07AC.svs
Time Statistics:
tiles_from_wsi      :  20.7199 s (36.71%)
encode_patches      :  35.7247 s (63.29%)
--------------------------------------------------
Total Time          :  56.4446 s (100.00%)
Speed               : 45.0 patches/sec



BLCA | Batches:  44%|████▍     | 7/16 [24:07:48<30:36:28, 12243.12s/it]

[CLEAN] batch 7: removed 30/30 file_id dirs.

===== [BLCA] Batch 8/16 | size=30 =====
[BATCH 8] 30/30 files need downloading


[PASS 1/3] gdc-client for batch 8
[GDC] CMD: /home/student2025/shirx2025/MUSK-surv/TCGA_DATA/gdc-client/gdc-client download -m /home/student2025/shirx2025/MUSK-surv/PATIENT_NPZ_FINAL/BLCA/tmpeewg1m22/gdc_manifest.BLCA.batch8.txt -d /home/student2025/shirx2025/MUSK-surv/TCGA_DATA/TCGA_BLCA
